# Capstone Project
## Problem : Where would be recommended if someone want to open a restaurant in Queens ?
The data will be get from the New York Geojson, and the Foursquare map. The data will contain only the 'food' categories and the distance to Flushing Main Street which represent traffic convenience. With these data, we can get the information of food shop density and traffic convenience. Then, with clustering analysis, we can know that neighborhood has similar characteristic.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


## Using the New York Geojson data

In [2]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

## Get the latitude and longitude of Flushing Main Street

In [18]:
address = 'Flushing Main Street'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of NY are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of NY are 40.7585195, -73.8298574.


In [4]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [17]:
print(neighborhoods.shape)
neighborhoods.head()

(306, 4)


Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

## Get the data of Queens

In [22]:
queen_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
print(queen_data.shape)
queen_data.head()

(81, 4)


Borough     Neighborhood   Latitude  Longitude
0  Queens          Astoria  40.768509 -73.915654
1  Queens         Woodside  40.746349 -73.901842
2  Queens  Jackson Heights  40.751981 -73.882821
3  Queens         Elmhurst  40.744049 -73.881656
4  Queens     Howard Beach  40.654225 -73.838138

In [6]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [7]:
CLIENT_ID = 'OA0DRW3PDAHDZFVOP4IXML5MMCNNMWQHBBU1ERAP1CTCIZLD' # your Foursquare ID
CLIENT_SECRET = '2F3HF1ZFTNCLO1F5IN2ZFILSZQQDXSNJROIOVB2R5IM2S0A3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OA0DRW3PDAHDZFVOP4IXML5MMCNNMWQHBBU1ERAP1CTCIZLD
CLIENT_SECRET:2F3HF1ZFTNCLO1F5IN2ZFILSZQQDXSNJROIOVB2R5IM2S0A3


In [31]:
cat = '4d4b7105d754a06374d81259'
LIMIT = 200
radius = 10000
sortP = 1
sec = 'food'

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}&sortByPopularity={}&section={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude,
    radius,
    LIMIT,
    cat,
    sortP,
    sec)

results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f2a0abc9f652e1fa329b575'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': 'With specials', 'key': 'specials'}]},
  'headerLocation': 'Queens',
  'headerFullLocation': 'Queens',
  'headerLocationGranularity': 'city',
  'query': 'food',
  'totalResults': 250,
  'suggestedBounds': {'ne': {'lat': 40.84851959000009,
    'lng': -73.71126221232828},
   'sw': {'lat': 40.66851940999991, 'lng': -73.94845258767171}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b3ea6eaf964a52058a025e3',
       'name': 'Peter Luger Steak House',
       'location': {'address': '225 Northern Blvd',
        'crossStreet': 'btwn Tain Dr & Merrivale Rd',
        'lat': 40.7772453732

In [32]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/Users/steventsai/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name            categories        lat        lng
0      Peter Luger Steak House            Steakhouse  40.777245 -73.727541
1                   Mexicocina    Mexican Restaurant  40.811837 -73.909512
2  Patsy's Pizza - East Harlem           Pizza Place  40.797108 -73.934626
3           Trinciti Roti Shop  Caribbean Restaurant  40.680314 -73.821202
4                Utopia Bagels            Bagel Shop  40.780054 -73.793723

In [33]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


In [36]:
distance = venues[0]['venue']['location']['distance']
type(distance)

int

In [39]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        cat = '4d4b7105d754a06374d81259'
        LIMIT = 200
        sortP = 1
        sec = 'food'
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}&sortByPopularity={}&section={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT,
            cat,
            sortP,
            sec)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'], 
            v['venue']['location']['distance'],
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue distance',
                  'Venue Category']
    
    return(nearby_venues)

In [40]:
Q_venues = getNearbyVenues(names=queen_data['Neighborhood'],
                                   latitudes=queen_data['Latitude'],
                                   longitudes=queen_data['Longitude']
                                  )

Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


In [41]:
print(Q_venues.shape)
Q_venues.head()

(1597, 8)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                                Venue  Venue Latitude  Venue Longitude  \
0                         Sugar Freak       40.764443       -73.916055   
1  New York City Bagel & Coffee House       40.765841       -73.919441   
2                       Neptune Diner       40.770788       -73.916890   
3         Brooklyn Bagel & Coffee Co.       40.764732       -73.916944   
4                       George's Deli       40.766316       -73.915284   

   Venue distance             Venue Category  
0             453  Cajun / Creole Restaurant  
1             436                 Bagel Shop  
2             274                      Diner  
3             434                 Bagel Shop  
4             246              Deli / Bodega

In [42]:
Q_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                   8                       8      8   
Astoria                                  89                      89     89   
Astoria Heights                          10                      10     10   
Auburndale                               11                      11     11   
Bay Terrace                              11                      11     11   
Bayside                                  60                      60     60   
Beechhurst                                7                       7      7   
Bellaire                                  8                       8      8   
Belle Harbor                              8                       8      8   
Bellerose                                16                      16     16   
Blissville                               11                      11     11   
Briarwood                                 5                       5      5   
Broad Channel                             5                       5      5   
Brookville                                2                       2      2   
Cambria Heights                           8                       8      8   
College Point                            45                      45     45   
Corona                                   22                      22     22   
Douglaston                               23                      23     23   
East Elmhurst                            10                      10     10   
Edgemere                                  4                       4      4   
Elmhurst                                 28                      28     28   
Far Rockaway                             24                      24     24   
Floral Park                               7                       7      7   
Flushing                                 69                      69     69   
Forest Hills                             24                      24     24   
Forest Hills Gardens                     19                      19     19   
Fresh Meadows                             5                       5      5   
Glen Oaks                                10                      10     10   
Glendale                                  7                       7      7   
Hammels                                   5                       5      5   
Hillcrest                                16                      16     16   
Hollis                                    5                       5      5   
Holliswood                                3                       3      3   
Howard Beach                             24                      24     24   
Hunters Point                            46                      46     46   
Jackson Heights                          61                      61     61   
Jamaica Center                           26                      26     26   
Jamaica Estates                           1                       1      1   
Jamaica Hills                            29                      29     29   
Kew Gardens                              31                      31     31   
Kew Gardens Hills                        15                      15     15   
Laurelton                                 4                       4      4   
Lefrak City                              21                      21     21   
Lindenwood                                7                       7      7   
Little Neck                              42                      42     42   
Long Island City                         46                      46     46   
Malba                                     1                       1      1   
Maspeth                                  27                      27     27   
Middle Village                           15                      15     15   
Murray Hill                              38 

In [43]:
print('There are {} unique categories.'.format(len(Q_venues['Venue Category'].unique())))

There are 97 unique categories.


In [44]:
# one hot encoding
Q_onehot = pd.get_dummies(Q_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Q_onehot['Neighborhood'] = Q_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Q_onehot.columns[-1]] + list(Q_onehot.columns[:-1])
Q_onehot = Q_onehot[fixed_columns]

Q_onehot.head()

Neighborhood  Afghan Restaurant  American Restaurant  Arepa Restaurant  \
0      Astoria                  0                    0                 0   
1      Astoria                  0                    0                 0   
2      Astoria                  0                    0                 0   
3      Astoria                  0                    0                 0   
4      Astoria                  0                    0                 0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           0       0   
1                       0                 0          0           1       0   
2                       0                 0          0           0       0   
3                       0                 0          0           1       0   
4                       0                 0          0           0       0   

   Bistro  Brazilian Restaurant  Breakfast Spot  Buffet  Burger Joint  \
0       0                     0               0       0             0   
1       0                     0               0       0             0   
2       0                     0               0       0             0   
3       0                     0               0       0             0   
4       0                     0               0       0             0   

   Burrito Place  Cafeteria  Café  Cajun / Creole Restaurant  \
0              0          0     0                          1   
1              0          0     0                          0   
2              0          0     0                          0   
3              0          0     0                          0   
4              0          0     0                          0   

   Cantonese Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                     0                     0                   0   
1                     0                     0                   0   
2                     0                     0                   0   
3                     0                     0                   0   
4                     0                     0                   0   

   Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
0                     0                        0                 0   
1                     0                        0                 0   
2                     0                        0                 0   
3                     0                        0                 0   
4                     0                        0                 0   

   Deli / Bodega  Dim Sum Restaurant  Diner  Donut Shop  Dosa Place  \
0              0                   0      0           0           0   
1              0                   0      0           0           0   
2              0                   0      1           0           0   
3              0                   0      0           0           0   
4              1                   0      0           0           0   

   Dumpling Restaurant  Eastern European Restaurant  Egyptian Restaurant  \
0                    0                            0                    0   
1                    0                            0                    0   
2                    0                            0                    0   
3                    0                            0                    0   
4                    0                            0                    0   

   Empanada Restaurant  Falafel Restaurant  Fast Food Restaurant  \
0                    0                   0                     0   
1                    0                   0                     0   
2                    0                   0                     0   
3                    0                   0                     0   
4                    0                   0                     0   

   Filipino Restaurant  Fish & Chips Shop  Food  Food Court  Food Stand  \
0                    0                  0     0 

In [45]:
Q_onehot.shape

(1597, 98)

In [46]:
Q_grouped = Q_onehot.groupby('Neighborhood').mean().reset_index()
Q_grouped

Neighborhood  Afghan Restaurant  American Restaurant  \
0                Arverne           0.000000             0.000000   
1                Astoria           0.000000             0.022472   
2        Astoria Heights           0.000000             0.000000   
3             Auburndale           0.000000             0.181818   
4            Bay Terrace           0.000000             0.181818   
5                Bayside           0.000000             0.050000   
6             Beechhurst           0.000000             0.000000   
7               Bellaire           0.000000             0.000000   
8           Belle Harbor           0.000000             0.000000   
9              Bellerose           0.000000             0.062500   
10            Blissville           0.000000             0.000000   
11             Briarwood           0.000000             0.000000   
12         Broad Channel           0.000000             0.000000   
13            Brookville           0.000000             0.000000   
14       Cambria Heights           0.000000             0.000000   
15         College Point           0.000000             0.000000   
16                Corona           0.000000             0.000000   
17            Douglaston           0.000000             0.000000   
18         East Elmhurst           0.000000             0.100000   
19              Edgemere           0.000000             0.000000   
20              Elmhurst           0.000000             0.000000   
21          Far Rockaway           0.000000             0.000000   
22           Floral Park           0.000000             0.000000   
23              Flushing           0.000000             0.000000   
24          Forest Hills           0.000000             0.000000   
25  Forest Hills Gardens           0.000000             0.000000   
26         Fresh Meadows           0.000000             0.000000   
27             Glen Oaks           0.000000             0.000000   
28              Glendale           0.000000             0.000000   
29               Hammels           0.000000             0.000000   
30             Hillcrest           0.000000             0.000000   
31                Hollis           0.000000             0.000000   
32            Holliswood           0.000000             0.000000   
33          Howard Beach           0.000000             0.000000   
34         Hunters Point           0.000000             0.043478   
35       Jackson Heights           0.000000             0.000000   
36        Jamaica Center           0.000000             0.076923   
37       Jamaica Estates           0.000000             0.000000   
38         Jamaica Hills           0.000000             0.000000   
39           Kew Gardens           0.000000             0.032258   
40     Kew Gardens Hills           0.000000             0.000000   
41             Laurelton           0.000000             0.000000   
42           Lefrak City           0.000000             0.000000   
43            Lindenwood           0.000000             0.000000   
44           Little Neck           0.000000             0.000000   
45      Long Island City           0.000000             0.021739   
46                 Malba           0.000000             0.000000   
47               Maspeth           0.000000             0.000000   
48        Middle Village           0.000000             0.000000   
49           Murray Hill           0.000000             0.000000   
50          North Corona           0.000000             0.000000   
51       Oakland Gardens           0.000000             0.000000   
52            Ozone Park           0.000000             0.000000   
53               Pomonok           0.000000             0.200000   
54        Queens Village           0.000000             0.000000   
55       Queensboro Hill           0.000000             0.000000   
56          Queensbridge           0.000000             0.000000   
57            Ravenswood           0.027027             0.000000   


In [47]:
Q_grouped.shape

(77, 98)

In [48]:
num_top_venues = 5

for hood in Q_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Q_grouped[Q_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
             venue  freq
0   Sandwich Place  0.25
1       Restaurant  0.12
2             Café  0.12
3       Donut Shop  0.12
4  Thai Restaurant  0.12


----Astoria----
                       venue  freq
0  Middle Eastern Restaurant  0.10
1              Deli / Bodega  0.08
2           Greek Restaurant  0.07
3          Indian Restaurant  0.07
4                Pizza Place  0.06


----Astoria Heights----
                venue  freq
0  Italian Restaurant   0.2
1       Deli / Bodega   0.2
2  Chinese Restaurant   0.2
3         Pizza Place   0.1
4              Bakery   0.1


----Auburndale----
                 venue  freq
0  American Restaurant  0.18
1   Italian Restaurant  0.18
2    Korean Restaurant  0.18
3        Deli / Bodega  0.09
4         Noodle House  0.09


----Bay Terrace----
                 venue  freq
0           Donut Shop  0.18
1          Pizza Place  0.18
2  American Restaurant  0.18
3               Bakery  0.09
4          Salad Place  0.09


----Bayside----
   

In [57]:
Q_venues.groupby([ 'Neighborhood', 'Venue Category']).mean()

Neighborhood Latitude  \
Neighborhood         Venue Category                                           
Arverne              Burrito Place                                40.589144   
                     Café                                         40.589144   
                     Donut Shop                                   40.589144   
                     Pizza Place                                  40.589144   
                     Restaurant                                   40.589144   
                     Sandwich Place                               40.589144   
                     Thai Restaurant                              40.589144   
Astoria              American Restaurant                          40.768509   
                     BBQ Joint                                    40.768509   
                     Bagel Shop                                   40.768509   
                     Bakery                                       40.768509   
                     Brazilian Restaurant                         40.768509   
                     Breakfast Spot                               40.768509   
                     Burger Joint                                 40.768509   
                     Café                                         40.768509   
                     Cajun / Creole Restaurant                    40.768509   
                     Chinese Restaurant                           40.768509   
                     Comfort Food Restaurant                      40.768509   
                     Deli / Bodega                                40.768509   
                     Diner                                        40.768509   
                     Falafel Restaurant                           40.768509   
                     Fast Food Restaurant                         40.768509   
                     Food                                         40.768509   
                     Food Truck                                   40.768509   
                     Greek Restaurant                             40.768509   
                     Halal Restaurant                             40.768509   
                     Indian Restaurant                            40.768509   
                     Irish Pub                                    40.768509   
                     Italian Restaurant                           40.768509   
                     Japanese Restaurant                          40.768509   
                     Korean Restaurant                            40.768509   
                     Latin American Restaurant                    40.768509   
                     Mediterranean Restaurant                     40.768509   
                     Mexican Restaurant                           40.768509   
                     Middle Eastern Restaurant                    40.768509   
                     Moroccan Restaurant                          40.768509   
                     New American Restaurant                      40.768509   
                     Pizza Place                                  40.768509   
                     Poke Place                                   40.768509   
                     Restaurant                                   40.768509   
                     Sandwich Place                               40.768509   
                     Seafood Restaurant                           40.768509   
                     Souvlaki Shop                                40.768509   
                     Sushi Restaurant                             40.768509   
                     Thai Restaurant                              40.768509   
                     Vegetarian / Vegan Restaurant                40.768509   
Astoria Heights      Bakery                                       40.770317   
                     Burger Joint                                 40.770317   
                     Chinese Restaurant                           40.770317   
                     Deli

## Define a function of calculating the distance of each venue to Flushing Main Street by longitude and latitude

In [61]:
import math
def distance_cal(lat1,lon1,lat2,lon2):
    R = 6137e3
    phi1 = lat1 * math.pi/180
    phi2 = lat2 * math.pi/180
    dphi = (lat2-lat1) * math.pi/180
    dlam = (lon2-lon1) * math.pi/180
    a = math.sin(dphi/2) * math.sin(dphi/2) + math.cos(phi1) * math.cos(phi2) * math.sin(dlam/2) * math.sin(dlam/2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    d = R * c
    return d

In [82]:
# Flushin Main Street latitude and longitude
lat1 = 40.7585195
lon1 = -73.8298574
# Calculate the distance to Flushing Main Street of each venue
dist_to_Flushing = []
for name, lat2, lon2 in zip(Q_venues['Venue'], Q_venues['Venue Latitude'], Q_venues['Venue Longitude']):
    d = distance_cal(lat1, lon1, lat2, lon2)
    dist_to_Flushing.append([name, int(d)])

dist_df = pd.DataFrame(dist_to_Flushing)
dist_df.rename(columns = {0:'Venue', 1:'Distance'}, inplace = True)

In [89]:
print(dist_df.shape)
dist_df

(1597, 2)


Venue  Distance
0                                           Sugar Freak      7021
1                    New York City Bagel & Coffee House      7309
2                                         Neptune Diner      7181
3                           Brooklyn Bagel & Coffee Co.      7096
4                                         George's Deli      6980
5                               Koroni Souvlaki & Grill      7485
6                                             The Grand      7056
7                           Al-sham Sweets and Pastries      6706
8                                           Butcher Bar      7039
9                                      Zyara Restaurant      6777
10                        Leli's Bakery and Pastry Shop      7161
11                                       Queens Comfort      7082
12                                     Nonna’s Pizzeria      6585
13                                               Mombar      6746
14                                          Burger Club      7409
15                                        Blend Astoria      6997
16                                      Sissy McGinty's      6796
17                                 New York Bakery Café      7389
18                                  Café To Go Creperie      7402
19                                 Ovelia Psistaria Bar      7264
20                                Farid Kebab, Steinway      6731
21                                       AbuQir Seafood      6683
22                                             Gyro Uno      6839
23                                            The Gully      6754
24                               Basil Brick Oven Pizza      7437
25                                           Gyro World      7132
26                                     Mochiron Izakaya      7229
27                                              Sabry's      6689
28                                   Grand Avenue Pizza      7206
29                                              SVL Bar      7294
30                            Dave and Tony's Salumeria      7218
31                                           Via Trenta      7072
32                                           Kabab Café      6728
33                                 Pochana Thai Kitchen      7295
34                                Elias Corner For Fish      7132
35                                       Little Morocco      6703
36                                            Pink Nori      7120
37                                         Off The Hook      7219
38                                        Crave Astoria      7120
39                                  Seva Indian Cuisine      7283
40                                         Poke Burrito      7039
41                                        Astoria Pizza      7396
42                            International Meat Market      7102
43                      Golden House Chinese Restaurant      7167
44                                                Duzan      6674
45                                            Viva Viva      7251
46                                          Jujube Tree      7200
47                                               Sampan      6908
48                                         Favela Grill      7204
49                                         Layali Dubai      6666
50                                        Kurry Qulture      7115
51                                                  Kal      7249
52                         Antika Restaurant & Pizzeria      7115
53                                             Pita Pan      7014
54                                   Tikka Indian Grill      7241
55                                    Café Via Espresso      6660
56                                       Golden Kitchen      7344
57                                            Azal Food      6714
58                                         AwesomeSauce      6643
59                                       Hangar Astoria      6877
60                      

In [105]:
Q_venues_d = pd.concat([Q_venues, dist_df['Distance']], axis = 1)
Q_venues_d.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                                Venue  Venue Latitude  Venue Longitude  \
0                         Sugar Freak       40.764443       -73.916055   
1  New York City Bagel & Coffee House       40.765841       -73.919441   
2                       Neptune Diner       40.770788       -73.916890   
3         Brooklyn Bagel & Coffee Co.       40.764732       -73.916944   
4                       George's Deli       40.766316       -73.915284   

   Venue distance             Venue Category  Distance  
0             453  Cajun / Creole Restaurant      7021  
1             436                 Bagel Shop      7309  
2             274                      Diner      7181  
3             434                 Bagel Shop      7096  
4             246              Deli / Bodega      6980

In [110]:
Q_venues_d.drop(['Venue distance'], axis = 1, inplace = True)

In [113]:
Q_venues_d

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                  Astoria              40.768509              -73.915654   
1                  Astoria              40.768509              -73.915654   
2                  Astoria              40.768509              -73.915654   
3                  Astoria              40.768509              -73.915654   
4                  Astoria              40.768509              -73.915654   
5                  Astoria              40.768509              -73.915654   
6                  Astoria              40.768509              -73.915654   
7                  Astoria              40.768509              -73.915654   
8                  Astoria              40.768509              -73.915654   
9                  Astoria              40.768509              -73.915654   
10                 Astoria              40.768509              -73.915654   
11                 Astoria              40.768509              -73.915654   
12                 Astoria              40.768509              -73.915654   
13                 Astoria              40.768509              -73.915654   
14                 Astoria              40.768509              -73.915654   
15                 Astoria              40.768509              -73.915654   
16                 Astoria              40.768509              -73.915654   
17                 Astoria              40.768509              -73.915654   
18                 Astoria              40.768509              -73.915654   
19                 Astoria              40.768509              -73.915654   
20                 Astoria              40.768509              -73.915654   
21                 Astoria              40.768509              -73.915654   
22                 Astoria              40.768509              -73.915654   
23                 Astoria              40.768509              -73.915654   
24                 Astoria              40.768509              -73.915654   
25                 Astoria              40.768509              -73.915654   
26                 Astoria              40.768509              -73.915654   
27                 Astoria              40.768509              -73.915654   
28                 Astoria              40.768509              -73.915654   
29                 Astoria              40.768509              -73.915654   
30                 Astoria              40.768509              -73.915654   
31                 Astoria              40.768509              -73.915654   
32                 Astoria              40.768509              -73.915654   
33                 Astoria              40.768509              -73.915654   
34                 Astoria              40.768509              -73.915654   
35                 Astoria              40.768509              -73.915654   
36                 Astoria              40.768509              -73.915654   
37                 Astoria              40.768509              -73.915654   
38                 Astoria              40.768509              -73.915654   
39                 Astoria              40.768509              -73.915654   
40                 Astoria              40.768509              -73.915654   
41                 Astoria              40.768509              -73.915654   
42                 Astoria              40.768509              -73.915654   
43                 Astoria              40.768509              -73.915654   
44                 Astoria              40.768509              -73.915654   
45                 Astoria              40.768509              -73.915654   
46                 Astoria              40.768509              -73.915654   
47                 Astoria              40.768509              -73.915654   
48                 Astoria              40.768509              -73.915654   
49                 Astoria              40.768509              -73.915654   
50                 Astoria              40.768509              -73.915654   
51        

## Get the average distance of all venues in the neighborhood

In [128]:
Q_distance_M = Q_venues_d.groupby('Neighborhood').mean()
Q_distance_M['Distance']

Neighborhood
Arverne                 18151.500000
Astoria                  7039.235955
Astoria Heights          5351.600000
Auburndale               3159.454545
Bay Terrace              4883.272727
Bayside                  4758.200000
Beechhurst               4143.714286
Bellaire                 8053.250000
Belle Harbor            19352.000000
Bellerose                9576.812500
Blissville               8597.545455
Briarwood                5411.400000
Broad Channel           16286.400000
Brookville              12248.500000
Cambria Heights         10517.500000
College Point            2879.622222
Corona                   2663.454545
Douglaston               7180.826087
East Elmhurst            3166.200000
Edgemere                18002.500000
Elmhurst                 4547.321429
Far Rockaway            17748.416667
Floral Park             10050.000000
Flushing                  486.594203
Forest Hills             4075.291667
Forest Hills Gardens     4508.368421
Fresh Meadows            

## Transfer dataframe by one hot encoding 

In [114]:
# one hot encoding
Q_onehot = pd.get_dummies(Q_venues_d[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Q_onehot['Neighborhood'] = Q_venues_d['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Q_onehot.columns[-1]] + list(Q_onehot.columns[:-1])
Q_onehot = Q_onehot[fixed_columns]

Q_onehot.head()

Neighborhood  Afghan Restaurant  American Restaurant  Arepa Restaurant  \
0      Astoria                  0                    0                 0   
1      Astoria                  0                    0                 0   
2      Astoria                  0                    0                 0   
3      Astoria                  0                    0                 0   
4      Astoria                  0                    0                 0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           0       0   
1                       0                 0          0           1       0   
2                       0                 0          0           0       0   
3                       0                 0          0           1       0   
4                       0                 0          0           0       0   

   Bistro  Brazilian Restaurant  Breakfast Spot  Buffet  Burger Joint  \
0       0                     0               0       0             0   
1       0                     0               0       0             0   
2       0                     0               0       0             0   
3       0                     0               0       0             0   
4       0                     0               0       0             0   

   Burrito Place  Cafeteria  Café  Cajun / Creole Restaurant  \
0              0          0     0                          1   
1              0          0     0                          0   
2              0          0     0                          0   
3              0          0     0                          0   
4              0          0     0                          0   

   Cantonese Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                     0                     0                   0   
1                     0                     0                   0   
2                     0                     0                   0   
3                     0                     0                   0   
4                     0                     0                   0   

   Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
0                     0                        0                 0   
1                     0                        0                 0   
2                     0                        0                 0   
3                     0                        0                 0   
4                     0                        0                 0   

   Deli / Bodega  Dim Sum Restaurant  Diner  Donut Shop  Dosa Place  \
0              0                   0      0           0           0   
1              0                   0      0           0           0   
2              0                   0      1           0           0   
3              0                   0      0           0           0   
4              1                   0      0           0           0   

   Dumpling Restaurant  Eastern European Restaurant  Egyptian Restaurant  \
0                    0                            0                    0   
1                    0                            0                    0   
2                    0                            0                    0   
3                    0                            0                    0   
4                    0                            0                    0   

   Empanada Restaurant  Falafel Restaurant  Fast Food Restaurant  \
0                    0                   0                     0   
1                    0                   0                     0   
2                    0                   0                     0   
3                    0                   0                     0   
4                    0                   0                     0   

   Filipino Restaurant  Fish & Chips Shop  Food  Food Court  Food Stand  \
0                    0                  0     0 

In [138]:
Q_grouped = Q_onehot.groupby('Neighborhood').mean().reset_index()
Q_grouped.sort_values(by='Neighborhood',inplace = True)
Q_grouped

Neighborhood  Afghan Restaurant  American Restaurant  \
0                Arverne           0.000000             0.000000   
1                Astoria           0.000000             0.022472   
2        Astoria Heights           0.000000             0.000000   
3             Auburndale           0.000000             0.181818   
4            Bay Terrace           0.000000             0.181818   
5                Bayside           0.000000             0.050000   
6             Beechhurst           0.000000             0.000000   
7               Bellaire           0.000000             0.000000   
8           Belle Harbor           0.000000             0.000000   
9              Bellerose           0.000000             0.062500   
10            Blissville           0.000000             0.000000   
11             Briarwood           0.000000             0.000000   
12         Broad Channel           0.000000             0.000000   
13            Brookville           0.000000             0.000000   
14       Cambria Heights           0.000000             0.000000   
15         College Point           0.000000             0.000000   
16                Corona           0.000000             0.000000   
17            Douglaston           0.000000             0.000000   
18         East Elmhurst           0.000000             0.100000   
19              Edgemere           0.000000             0.000000   
20              Elmhurst           0.000000             0.000000   
21          Far Rockaway           0.000000             0.000000   
22           Floral Park           0.000000             0.000000   
23              Flushing           0.000000             0.000000   
24          Forest Hills           0.000000             0.000000   
25  Forest Hills Gardens           0.000000             0.000000   
26         Fresh Meadows           0.000000             0.000000   
27             Glen Oaks           0.000000             0.000000   
28              Glendale           0.000000             0.000000   
29               Hammels           0.000000             0.000000   
30             Hillcrest           0.000000             0.000000   
31                Hollis           0.000000             0.000000   
32            Holliswood           0.000000             0.000000   
33          Howard Beach           0.000000             0.000000   
34         Hunters Point           0.000000             0.043478   
35       Jackson Heights           0.000000             0.000000   
36        Jamaica Center           0.000000             0.076923   
37       Jamaica Estates           0.000000             0.000000   
38         Jamaica Hills           0.000000             0.000000   
39           Kew Gardens           0.000000             0.032258   
40     Kew Gardens Hills           0.000000             0.000000   
41             Laurelton           0.000000             0.000000   
42           Lefrak City           0.000000             0.000000   
43            Lindenwood           0.000000             0.000000   
44           Little Neck           0.000000             0.000000   
45      Long Island City           0.000000             0.021739   
46                 Malba           0.000000             0.000000   
47               Maspeth           0.000000             0.000000   
48        Middle Village           0.000000             0.000000   
49           Murray Hill           0.000000             0.000000   
50          North Corona           0.000000             0.000000   
51       Oakland Gardens           0.000000             0.000000   
52            Ozone Park           0.000000             0.000000   
53               Pomonok           0.000000             0.200000   
54        Queens Village           0.000000             0.000000   
55       Queensboro Hill           0.000000             0.000000   
56          Queensbridge           0.000000             0.000000   
57            Ravenswood           0.027027             0.000000   


In [149]:
Q_mergeD = Q_grouped.merge(Q_distance_M, on = 'Neighborhood')

In [150]:
Q_mergeD.drop(columns=['Distance to Flushing', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue Latitude', 'Venue Longitude',], axis = 1)

Neighborhood  Afghan Restaurant  American Restaurant  \
0                Arverne           0.000000             0.000000   
1                Astoria           0.000000             0.022472   
2        Astoria Heights           0.000000             0.000000   
3             Auburndale           0.000000             0.181818   
4            Bay Terrace           0.000000             0.181818   
5                Bayside           0.000000             0.050000   
6             Beechhurst           0.000000             0.000000   
7               Bellaire           0.000000             0.000000   
8           Belle Harbor           0.000000             0.000000   
9              Bellerose           0.000000             0.062500   
10            Blissville           0.000000             0.000000   
11             Briarwood           0.000000             0.000000   
12         Broad Channel           0.000000             0.000000   
13            Brookville           0.000000             0.000000   
14       Cambria Heights           0.000000             0.000000   
15         College Point           0.000000             0.000000   
16                Corona           0.000000             0.000000   
17            Douglaston           0.000000             0.000000   
18         East Elmhurst           0.000000             0.100000   
19              Edgemere           0.000000             0.000000   
20              Elmhurst           0.000000             0.000000   
21          Far Rockaway           0.000000             0.000000   
22           Floral Park           0.000000             0.000000   
23              Flushing           0.000000             0.000000   
24          Forest Hills           0.000000             0.000000   
25  Forest Hills Gardens           0.000000             0.000000   
26         Fresh Meadows           0.000000             0.000000   
27             Glen Oaks           0.000000             0.000000   
28              Glendale           0.000000             0.000000   
29               Hammels           0.000000             0.000000   
30             Hillcrest           0.000000             0.000000   
31                Hollis           0.000000             0.000000   
32            Holliswood           0.000000             0.000000   
33          Howard Beach           0.000000             0.000000   
34         Hunters Point           0.000000             0.043478   
35       Jackson Heights           0.000000             0.000000   
36        Jamaica Center           0.000000             0.076923   
37       Jamaica Estates           0.000000             0.000000   
38         Jamaica Hills           0.000000             0.000000   
39           Kew Gardens           0.000000             0.032258   
40     Kew Gardens Hills           0.000000             0.000000   
41             Laurelton           0.000000             0.000000   
42           Lefrak City           0.000000             0.000000   
43            Lindenwood           0.000000             0.000000   
44           Little Neck           0.000000             0.000000   
45      Long Island City           0.000000             0.021739   
46                 Malba           0.000000             0.000000   
47               Maspeth           0.000000             0.000000   
48        Middle Village           0.000000             0.000000   
49           Murray Hill           0.000000             0.000000   
50          North Corona           0.000000             0.000000   
51       Oakland Gardens           0.000000             0.000000   
52            Ozone Park           0.000000             0.000000   
53               Pomonok           0.000000             0.200000   
54        Queens Village           0.000000             0.000000   
55       Queensboro Hill           0.000000             0.000000   
56          Queensbridge           0.000000             0.000000   
57            Ravenswood           0.027027             0.000000   
